# Part 2: Heat map with overlay of police districts

## 0 Preamble

### 0.1 Imports and constants

In [1]:
import calendar
import folium
from folium.plugins import HeatMap, HeatMapWithTime
import json
import matplotlib.pyplot as plt
import pandas as pd
import plotly.express as px
import os

### 0.2 Loading and cleaning data from files

In [2]:
# Loading the data and files
data_path = os.path.abspath(os.path.join(os.pardir, "data"))
files_path = os.path.abspath(os.path.join(os.pardir, "files"))

# Read shapefile from the provided geojson file
geojson_name = "sfpd.geojson"
geojson_path = os.path.join(files_path, geojson_name)

# Open geojson data to load shape of police districts
with open(geojson_path) as response:
    counties = json.load(response)

# Load csv data into pandas dataframe
cleaned_data_path = os.path.join(data_path, "Police_Department_Incident_Reports_Complete.csv")
df = pd.read_csv(cleaned_data_path)

# Define focus crimes
focuscrimes = set([
    'DRUG/NARCOTIC',
])

# Filter and clean data for focus crimes
df_focus = df[df['Category'].isin(focuscrimes)].fillna(0)
# df_focus = df_sample[df_sample["Year"].isin([2019, 2020])]

# Create a Date column by combining Year, Month, and Day
df_focus["Date"] = pd.to_datetime(df_focus[["Year", "Month", "Day"]])

In [3]:
# Display geojson
# counties["features"][0]

In [4]:
# Display dataframe
# df_focus

## 1 Find the center point of the GeoJSON locations

### 1.1 Helper functions

In [5]:
# Find the minimum and maximum longitude and latitude values
def get_min_max_from_feature(data):
    lon_min, lon_max = (min(x[0] for x in data), max(x[0] for x in data))
    lat_min, lat_max = (min(x[1] for x in data), max(x[1] for x in data))
    return lon_min, lon_max, lat_min, lat_max

In [6]:
# Get the minimum and maximum longitude and latitude values from geojson
def get_min_max_lon_lat(geojson):
    lons = []
    lats = []
    for feat in geojson["features"]:
        if feat["geometry"]["type"] == "Polygon":
            f = feat["geometry"]["coordinates"][0]
            lon_min, lon_max, lat_min, lat_max = get_min_max_from_feature(f)
            lons.append(lon_min)
            lons.append(lon_max)
            lats.append(lat_min)
            lats.append(lat_max)
        elif feat["geometry"]["type"] == "MultiPolygon":
            for poly in feat["geometry"]["coordinates"]:
                f = poly[0]
                lon_min, lon_max, lat_min, lat_max = get_min_max_from_feature(f)
                lons.append(lon_min)
                lons.append(lon_max)
                lats.append(lat_min)
                lats.append(lat_max)
    return min(lons), max(lons), min(lats), max(lats)

In [7]:
# Find center of the map
def get_center_lon_lat(geojson):
    lon_min, lon_max, lat_min, lat_max = get_min_max_lon_lat(geojson)
    return [(lon_max + lon_min) / 2, (lat_max + lat_min) / 2]

### 1.2 Calculate center of San Fransisco data

In [8]:
# Get the center of the map
sf_coords = get_center_lon_lat(counties)
sf_coords

[-122.43596572128945, 37.7706886371677]

## 2 Prepare GeoJSON data for overlay

### 2.1 Update GeoJSON data with aggregated no. of incidents per month/year

In [9]:
# Convert (Year, Month) into "YYYY - MonthName"
df_focus["Time_Key"] = df_focus.apply(lambda row: f"{row['Year']} - {calendar.month_name[row['Month']]}", axis=1)
# df_focus["Time_Key"] = df_focus.apply(lambda row: f"{row['Year']} - {row['Month']:02d}", axis=1)

# Group data using new Time_Key format
district_time_data = df_focus.groupby(["Time_Key", "Police District"]).size().unstack(fill_value=0)

# Convert to a JavaScript-friendly dictionary
district_time_js = district_time_data.to_dict(orient="index")

# Convert dictionary to JSON for JavaScript usage
district_time_json = json.dumps(district_time_js)

# Store json locally with HTML
json_path = os.path.join(files_path, "incident_data.json")
with open(json_path, 'w') as f:
    json.dump(district_time_json, f)

In [10]:
# List of all timestamps ("year - month")
district_time_js_list = list(district_time_js)

for idx in range(len(counties["features"])):

    # Get district from feature by idx
    dist_id = counties["features"][idx]["properties"]["DISTRICT"]
    
    # Initialize the dictionary
    counties["features"][idx]["properties"]["times"] = []
    counties["features"][idx]["properties"]["NO_OF_INCIDENTS"] = []

    for timestamp in district_time_js_list:
        counties["features"][idx]["properties"]["times"].append(timestamp)
        counties["features"][idx]["properties"]["NO_OF_INCIDENTS"].append(district_time_js[timestamp][dist_id])

    counties["features"][idx]["properties"]["tooltip"] = {"fields" : ["DISTRICT", "NO_OF_INCIDENTS"], "aliases" : ["District:", "No. of incidents:"]}

In [11]:
print(counties["features"][0]["properties"]["DISTRICT"])
print(counties["features"][0]["properties"]["times"][:5])
print(counties["features"][0]["properties"]["NO_OF_INCIDENTS"][:5])
print(counties["features"][0]["properties"]["tooltip"])

CENTRAL
['2003 - April', '2003 - August', '2003 - December', '2003 - February', '2003 - January']
[41, 21, 29, 33, 26]
{'fields': ['DISTRICT', 'NO_OF_INCIDENTS'], 'aliases': ['District:', 'No. of incidents:']}


### 2.2 Create default map

In [12]:
# Create a map around San Francisco's center point
folium_heatmap_timeseries = folium.Map(location=[sf_coords[1], sf_coords[0]], zoom_start=12, tiles="cartodbpositron")

### 2.3 Add borders of Police Districts from GeoJSON data to map

In [13]:
# Parse geojson data into the heatmap
folium.GeoJson(
    counties,
    name = "Police Districts",
    highlight_function=lambda feature: {
        "fillColor": "#FFCC00",
        "fillOpacity": 0.3,
        "weight": 2.0,
        "dashArray": "1, 1",
    },
    style_function = lambda feature: {
        "fillColor": "white",
        "color": "black",
        "weight": 1.0,
        "fillOpacity": 0,
        "dashArray": "3, 3",
    },
).add_to(folium_heatmap_timeseries)

In [14]:
# Show with borders added
folium_heatmap_timeseries

##  3 Create heatmap

###  3.1 Generate heatmap data

In [15]:
# Group by date and create heat data
heat_data = []
for date, group in df_focus.groupby([
    'Year',
    'Month', 
    ]):
    heat_data.append(group[['Latitude (Y)', 'Longitude (X)']].values.tolist())

### 3.2 Create timestamps for each month/year

In [16]:
# Create the indicies for the frames, i.e. the titles of the frames
time_index = [date.strftime("%Y - %B") for date in sorted(df_focus['Date'].dt.to_period('M').unique().to_timestamp())]
# time_index = [*df_focus['Date'].dt.to_period('M').unique().strftime("%Y - %m")]
# time_index = [*df_focus["Time_Key"].unique()]
time_index[:12]

['2003 - January',
 '2003 - February',
 '2003 - March',
 '2003 - April',
 '2003 - May',
 '2003 - June',
 '2003 - July',
 '2003 - August',
 '2003 - September',
 '2003 - October',
 '2003 - November',
 '2003 - December']

### 3.3 Add heat map data to folium map

In [17]:
# Add heat map to folium map
HeatMapWithTime(
    heat_data,
    index=time_index,
    radius=15,
    blur=0.8,
    min_opacity=0.0,
    max_opacity=0.6,
    min_speed=1, 
    max_speed=12, 
    auto_play=True,
    use_local_extrema=True
).add_to(folium_heatmap_timeseries)

### 3.4 Store HTML locally

In [18]:
# Save and Display
heatmap_path = os.path.join(files_path, "A2_san_francisco_heatmapwithtime.html")
folium_heatmap_timeseries.save(heatmap_path)
folium_heatmap_timeseries